# Create smooth elevation contours

This application will produce smooth elevation contours from DSMs and DEMs. 

![Contours for import to Mapbox](https://nyc3.digitaloceanspaces.com/astoria/geo409/images/Scene-CaveRunLake.jpg)
*3d contours for Cave Run Lake Dam shown in an ArcGIS Pro Local Scene*

In [ ]:
################ DO NOT EDIT ################ 
# 
# Import ArcGIS package
import arcpy
# Subprocess allows us to issue commands on the command line
import subprocess
# Zip utlity to extract files
from zipfile import ZipFile
# zip up a directory
import shutil

# Function definitions 
def makeAoi(lat, lon, dist, output, square=True):
    """Function to create round or square area of interest for lat, lon coordinate
    Parameters:
        lat = latitude (Number)
        lon = longitude (Number)
        dist = buffer distance (Number or valid string for Buffer function)
        output = workspace polygon layer name (String)
        square {optional} = square (default) or circular aoi polygon
    """
    out1 = f'{output}_pt_temp'
    out2 = f'{output}_round_temp'
    arcpy.env.addOutputsToMap = False
    wgs84 = arcpy.SpatialReference(4326)
    point = arcpy.Point(lon, lat) 
    ptGeometry = arcpy.PointGeometry(point, wgs84)
    arcpy.management.CopyFeatures(ptGeometry, out1)
    if square:
        arcpy.analysis.Buffer(out1, out2, dist)
        arcpy.env.addOutputsToMap = True
        arcpy.management.FeatureEnvelopeToPolygon(out2, output)
        arcpy.management.Delete(out2)
    else:
        arcpy.env.addOutputsToMap = True
        arcpy.analysis.Buffer(out1, output, dist)
    arcpy.management.Delete(out1)
    

In [ ]:
################### EDIT ################### 
# 
# Set global variables for project.
#
# Directory for your root GIS folder
root = "c:\\YodasGIS"

# Project name - creates a folder in project directory, if it doesn't already exist
project = "Contouring"

# Output geodatabase
workspace = "Contouring.gdb"

# Overwrite any existing output
arcpy.env.overwriteOutput = True

# Set coordinate system to Kentucky
ky = arcpy.SpatialReference(3089)
arcpy.env.outputCoordinateSystem = ky

In [ ]:
################ DO NOT EDIT ################ 
# 
# Create project workspace and default geodatabase if they do not exist.
#
filepath = f'{root}\\{project}'
subprocess.run(f'mkdir {filepath}', shell=True)
subprocess.run(f'mkdir {filepath}\\shapefiles', shell=True)
if arcpy.Exists(f'{filepath}\\{workspace}'):
    print(f'{filepath}\\{workspace} exists!')
else:
    print(f"Creating {filepath}\\{workspace}")
    arcpy.CreateFileGDB_management(filepath, workspace)
arcpy.env.workspace = f'{filepath}\\{workspace}'
completed = subprocess.run(f'dir {filepath}', shell=True, stdout=subprocess.PIPE)
print(completed.stdout.decode('UTF-8'))

print("Finished")

In [ ]:
################### EDIT ################### 
# 
# Set AOI
#
# Define the variables
lat = 37.7860232
lon = -84.7040941
dist = '1 Mile' # 1 mile buffer
output = 'herrington_dam_1mi'

# Make function call
makeAoi(lat, lon, dist, output)

# Extract DEM or DSM
dsm = 'https://kyraster.ky.gov/arcgis/rest/services/ElevationServices/Ky_DSM_First_Return_5FT_Phase1/ImageServer'
dem = 'https://kyraster.ky.gov/arcgis/rest/services/ElevationServices/Ky_DEM_KYAPED_5FT/ImageServer'

elev = arcpy.sa.ExtractByMask(dem, output)

print("Finished")

elev

In [ ]:
################### EDIT ################### 
# 
# Set coontouring variables for project.
#
# Set contour parameters
# Elevation layers created from previous module on lidar and 3D mapping

# Contour interval in feet.
contour_interval = 5

# Index contour, e.g., which interval should be labeled?
contour_index = 100

# Smoothing factor: number of cells from center to calculate in neighbrhood.
smooth = 5

################ DO NOT EDIT ################ 
# 
# Create names for output layers
#
contour_name = f"{output}_contour_{contour_interval}ft"
smoothedSurface = f"{output}_smooth_{smooth*10}ft"

print("Finished")

## Focal Statistics

Focal statistics geoprocessing function iterates over the input raster, cell-by-cell, and does statistics on a neighborhood of adjacent cells. It recalculates the input cell with the derived statistic. 

![Example of finding the SUM of cell values in the neighborhood of 1 cell](https://pro.arcgis.com/en/pro-app/latest/tool-reference/spatial-analyst/GUID-A8B2B309-AA73-478F-AFF7-B393CB23B1F7-web.png)    
*Example of finding the SUM of cell values in the neighborhood of 1 adjacent cell*

In our application, we're looking out with a radius set in the `smooth` variable and calculate the mean elevation value for the neighborhood. This calculation will smooth our elevation surface; higher `smooth` values will result in a smoother surface.

Please read the [tool documentation](https://pro.arcgis.com/en/pro-app/latest/tool-reference/spatial-analyst/focal-statistics.htm)

In [ ]:
################ DO NOT EDIT ################ 
# 
# Created the smooth elevation model to interpolate elevation contours
#
# Calculate the neighborhood using ArcPy Class NbrCircle(radius, units)
neighborhood = arcpy.sa.NbrCircle(smooth,'CELL')

# Calculate new raster surface uisng ArcPy Geoprocessing function FocalStatistics(in_raster, neighborhood, statistic)
outFocalStat = arcpy.sa.FocalStatistics(elev, neighborhood, "MEAN")

print("Finished")

# Print the raster to verify
outFocalStat

## Contouring

"Contours are lines that connect locations of equal value in a raster dataset that represents continuous phenomena such as elevation, temperature, precipitation, pollution, or atmospheric pressure."

Please read the [tool documentation](https://pro.arcgis.com/en/pro-app/latest/tool-reference/3d-analyst/contour.htm)

In [ ]:
################ DO NOT EDIT ################ 
# 
# Created feature class of contour lives fro elevation surface
#
# Function: Contour(in_raster, out_polyline_features, contour_interval)
arcpy.Contour_3d (outFocalStat, contour_name, contour_interval)

print("Finished")

## Adding attributes for index contour

An index contour is the contour that is symbolized more prominently and labeled on the map. Having an attribute the identifies it as an index makes it easier to symbolize. We'll use the modulo division operator `%` to calculate if an contour is divisible by large whole number without a remainder. E.g., 800 divided by 100 has a remainder of 0, so we could say it's an index contour using an index value of 100.

Tool Documentation
* [Add field](https://pro.arcgis.com/en/pro-app/latest/tool-reference/data-management/add-field.htm)
* [Calculate field](https://pro.arcgis.com/en/pro-app/latest/tool-reference/data-management/calculate-field.htm)


In [ ]:
################ DO NOT EDIT ################ 
# 
# Find index contours and label them in a new field
#
y = contour_index

code_block = """
def is_index_contour(x, y):
    if x % y == 0:
        return 1
    else:
        return 0
"""     
arcpy.AddField_management (contour_name, "index", "SHORT")        
arcpy.CalculateField_management(contour_name, "index", f"is_index_contour(!CONTOUR!, {y})", "PYTHON3", code_block)

print("Finished")

In [ ]:
################ DO NOT EDIT ################ 
# 
# Convert contours to a Shapefile
#
arcpy.conversion.FeatureClassToShapefile(contour_name, f'{root}\\{project}\\shapefiles')

print("Finished")

In [ ]:
################ DO NOT EDIT ################ 
# 
# Create archive of ShapeFile for upload to web mapping platforms
#
shutil.make_archive(f"{root}\\{project}\\{contour_name}_{project}", 'zip',  f'{root}\\{project}\\shapefiles')

print("Finished")

In [ ]:
help(shutil.make_archive)

## Find cliffs and steep areas

Using focal statistics and Map Algebra, we can find areas with a large elevation range in short horizontal distance using the Z `RANGE` statistic.

[Map Algebra](https://pro.arcgis.com/en/pro-app/latest/help/analysis/spatial-analyst/mapalgebra/a-quick-tour-of-using-map-algebra.htm)

In [ ]:
################### EDIT ################### 
# 
# Set focal statistics variable
#

# Number of cells from center to calculate in neighbrhood.
radius = 5

In [ ]:
################ DO NOT EDIT ################ 
# 
# Created the smooth elevation model to interpolate elevation contours
#
# Calculate the neighborhood using ArcPy Class NbrCircle(radius, units)
neighborhood = arcpy.sa.NbrCircle(radius,'CELL')

# Calculate new raster surface uisng ArcPy Geoprocessing function FocalStatistics(in_raster, neighborhood, statistic)
outZrange = arcpy.sa.FocalStatistics(elev, neighborhood, "RANGE")

print("Finished")

# Print the raster to verify
outZrange

In [ ]:
################### EDIT ################### 
# 
# What height do you want to find?
#
# All cells greater than the z value will be output to a new layer
#
z = 40

################ DO NOT EDIT ################ 
# 
# Map Algebra statement
#
cliffs = arcpy.sa.Con((outZrange > z), outZrange)

print("Finished")

# Print the raster to verify
cliffs

In [ ]:
################ DO NOT EDIT ################ 
# 
# Save temporary layer to new file
#
cliffs.save(f"Z{z}ft_H{radius*10}ft")

# This shows that within 50 ft of these cells, the elevation range is greater than 40 ft; >80% grade or slope.
# Check your ouput geodatabase to find this layer.